---

# S04E01 : Context managers - The with statement

Cyril Desjouy

---


## 1. Gestion des ressources avec les *context managers*

La principale utilité d'un *context manager* est de gérer les ressources. C'est la raison pour laquelle on l'utilise en particulier pour la lecture de fichiers. En effet, ouvrir un fichier consomme une ressource et ce nombre de ressources est limité par l'OS. 

Pour ouvrir et lire le contenu d'un fichier, on peut classiquement écrire:

In [2]:
file = open('quote.txt')
txt = file.read()
file.close()

print(txt)

“Bad programmers worry about the code.
Good programmers worry about data structures and their relationships.”
― Linus Torvalds



Avec cette formulation, il est très facile d'oublier de fermer le fichier avec la méthode `close()`. Dans le cas où le fichier est ouvert en écriture, cela peut mener à des résultats inattendus. Dans le cas où le fichier est ouvert en lecture, l'oubli n'est pas si grave, mais lorsqu'il s'agit de centaines de fichiers, cela peut mener à des situations critiques où les limites de l'OS peuvent par exemple être atteintes. En confiant la gestion des ressources à un *context manager*, on s'assure que chaque ressource est proprement fermée. 

En utilisant l'instruction `with... as...`, il est possible de retourner un *context manager* associé à un nom de variable qui sera disponible dans tout le bloc indenté:
```python
with ressource as name:
    do stuff
```

Pour ouvrir un fichier il suffit alors d'écrire:

In [5]:
with open('quote.txt') as file:
    txt = file.read()
    
print(txt)

“Bad programmers worry about the code.
Good programmers worry about data structures and their relationships.”
― Linus Torvalds



## 2. *Context managers* personnalisés

### 2.1. Les méthodes spéciales `__enter__` et `__exit__`

Pour implémenter un *context manager* personnalisé, il suffit d'écrire une classe contenant les méthodes spéciales `__enter__` et `__exit__`.

* `__enter__` peut retourner un objet qui sera assigné au nom après `as` (`None` par défaut). Il est courant de retourner `self` afin de garder toutes les fonctionnalités de la classe.
* `__exit__` qui doit libérer les ressources utilisées.

Par exemple:

In [3]:
class context:
    
    def __init__(self):
        print('Init context')
    
    def __enter__(self):
        print('Entering context manager')
        return self
        
    def __exit__(self, *args):
        print('Exiting context manager')

In [4]:
with context() as c:
    print("I'm in!")

Init context
Entering context manager
I'm in!
Exiting context manager


### 2.2. La gestion des exceptions

La méthode spéciale `__exit__` prend en fait 4 arguments d'entrée (d'où la présence du `*args` dans l'exemple précédent):

* l'instance
* `exception_type`: le type d'exception levée 
* `exception_value`: la valeur de l'exception levée
* `traceback`: le traceback

Le mécanisme de sortie proposé par les *context managers* permet de fermer correctement la ressource même si une exception a été levée au sein même du *context manager*. La méthode `__exit__` peut également retourner un booléen. Si ce booléen est `True`, alors les exceptions levées dans le bloc indenté seront cachées. Les exemples suivants illustent ceci :

**Note:** *Si une exception est levée dans la méthode `__init__` ou `__enter__` alors la méthode `__exit__` ne sera pas exécutée.*

In [22]:
class context:
    
    def __init__(self, noexception=False):
        self.noexception = noexception
        print('Init context')
    
    def __enter__(self):
        print('Entering context manager')
        return self
        
    def __exit__(self, exception_type, exception_value, traceback):
        
        if exception_type:
            print('type:', exception_type)
            print('value:', exception_value)
            print('traceback', traceback)
        
        print('Exiting context manager')
        return self.noexception
    
    def causes_exception(self):
        """ Deliberately causes an attribute error"""
        a = int('string')

In [23]:
with context(noexception=True) as c:
    c.causes_exeption()

Init context
Entering context manager
type: <class 'AttributeError'>
value: 'context' object has no attribute 'cause_exeption'
traceback <traceback object at 0x7fbe05f7a2d0>
Exiting context manager


In [25]:
with context() as c:
    c.causes_exeption()

Init context
Entering context manager
type: <class 'AttributeError'>
value: 'context' object has no attribute 'causes_exeption'
traceback <traceback object at 0x7fbe05f61370>
Exiting context manager


AttributeError: 'context' object has no attribute 'causes_exeption'

## 3. Utilisation des *context managers*

Les *context managers* sont très présents dans la bibliothèque standard. Ils sont loin d'être utilisés uniquement pour la gestion des fichiers textes. Voici quelques exemples d'applications:

* Les primitives de synchronisation de `threading`, `multiprocessing`, et `concurrent.futures` telles que les `Lock`, les `Semaphore`, les `Condition`, ... (cf notebook sur les primitives de synchronisation)
* Les fichiers zip (`zipfile.ZipFile)`, tar (`tarfile.TarFile`), ...
* Les ressources réseau
* La décoration
* ...


## Bibliographie

* [Jeffknupp.com - Python with context manager](https://jeffknupp.com/blog/2016/03/07/python-with-context-managers/)
* [Aly Sivji - Managing ressources with context managers](https://alysivji.github.io/managing-resources-with-context-managers-pythonic.html)

## Application

<div class="alert alert-block alert-info">
Implémentez un context manager permettant de mesurer le temps passé à exécuter une suite d'instructions. Vous utiliserez pour ce faire la fonction <code>perf_counter()</code> du module <code>time</code>.
</div>